In [181]:
import math
import numpy as np
from random import *
import time

In [235]:
# on calcule a^n mod N grâce à l'exponentiation rapide 
def Base(n,b): #Ecriture de n en base b
    L=[]
    while n>0:
        L=L+[n%b]
        n=n//b
    return L  

def ExpRapide(a,n,N): #Calcul de a^n modulo N par exponentiation rapide. 
    L=Base(n,2)
    P=[a%N]
    i=0
    while i<len(L)-1: #Calcul des carrés itérés de a modulo N
        b=(P[i]*P[i])%N
        P=P+[b]
        i=i+1
    p=1
    for i in range(len(L)): #Calcul le produit des carrés itérés de a associés aux coefficients non nuls de L
        if L[i]!=0:
            p=(p*P[i])%N
    return p    

In [236]:
# renvoie True a^{n-1} = 1 mod n pour tout a premier à n (cf condition (1) du TP 
# et renvoie False sinon
def TestFermat(n):
    for a in range(1,n):
        if math.gcd(a,n)==1 and ExpRapide(a,n-1,n) != 1:
            return False
    return True
        

In [237]:
for n in range(2,19):
    print(n,TestFermat(n))

2 True
3 True
4 False
5 True
6 False
7 True
8 False
9 False
10 False
11 True
12 False
13 True
14 False
15 False
16 False
17 True
18 False


In [238]:
# renvoie la liste des entiers n <= x tels que TestFermat(n) = True
def PremierFermat(x):
    L = []  # liste des entiers à renvoyer
    for n in range(2,x+1): # on parcourt les entiers entre 2 et x
        if TestFermat(n):  # si TestFermat(n) = True on ajoute n à notre liste
            L = L+[n]
    return L

In [239]:
PremierFermat(50)

[2, 3, 5, 7, 11, 13, 17, 19, 23, 29, 31, 37, 41, 43, 47]

In [240]:
# on supprime l'élément e (avec répétitions éventuelles) de la liste L
# sous-algo utilisé dans crible
def supprElemListe(L,e):
    N = L.count(e)  # on compte le nombre de fois où e apparaît dans la liste L
    for i in range(N): # on supprime e le nombre de fois où il apparaît
        L.remove(e)
    return L

In [241]:
# renvoie la liste des nombres premiers <= n en utilisant le crible d'Eratosthène
def crible(n):
    d=list(range(n+1)) # d est la liste des entiers entre 0 et n
    if n > 0: # 1 n'est pas premier
        d[1]=0
    r=2 #on initialise à p=2
    while r<math.sqrt(n)+1: # on peut arrêter le crible dès qu'on est plus grand que racine de n (1ère optimisation)
        if d[r]!=0: # on vérifie que le d[r] n'a pas déjà été supprimé (2ème optimisation)
            for i in range(r*r,n+1,r): #on "supprime" les multiples de r (en commençant à r^2) en mettant leur valeur à 0
                d[i]=0
        r=r+1   
    return supprElemListe(d,0);

In [242]:
# la liste PremierFermat(N) contient tous les nombres premiers, donc contient crible(N)
# On remarque que pour N = 3000 il y a 5 entiers qui sont dans PremierFermat(N) mais 
# pas dans crible(N). Ces entiers ne sont donc pas des nombres premiers!

N = 3000
print(len(PremierFermat(N)))
print(len(crible(N)))

435
430


In [243]:
# renvoie la liste des k premiers contre-exemples (qui ne sont pas Fermatpremiers mais pas premiers)
# horrible temps de calcul, plusieurs minutes pour calculer pour k=2
# cet algorithme n'est pas recommandé, il y a beaucoup de répétition de calculs
def contreExemples(k):
    n = 2
    L = []  # liste des contre-exemples
    j= 0   # compte le nombre de contre-exemples trouvés
    for j in range(k): 
        # on compare simplement la taille des listes
        # dès qu'il y a un saut de taille, c'est qu'on vient de trouver un contre-exemple
        while len(PremierFermat(n)) == len(crible(n))+j: 
            n =  n + 1  
        L = L+[n]    
    return L


In [31]:
contreExemples(1)

[561]

In [244]:
# On teste si un nombre est premier
# sous-algo utilisé dans contreExemples2
def isPrime(n):
    for i in range(2,int(n**0.5)+1):
        if n%i==0:
            return False       
    return True

In [245]:
# On code une deuxième version de PremierFermat qui renvoie un couple de booléens (b1,b2)
# b1 = True si n est premier, False sinon, et b2 = True si est premier de Fermat, False sinon
# En faisant cela on optimise un peu l'algo contreExemples2 ci-dessous


def TestFermat2(n):
    Prime = True  # change en false si n n'est pas premier
    for a in range(1,n):
        if math.gcd(a,n) != 1:
            Prime = False
        elif ExpRapide(a,n-1,n) != 1: # si n n'est pas premier de Fermat, il n'est pas non plus premier
            return (False,False)
    return (Prime,True)

In [246]:
# renvoie la liste des k premiers contre-exemples (qui ne sont pas premiers) en un temps 
# "raisonnable"
def contreExemples2(k):
    L = []  # liste des contre-exemples à renvoyer
    n = 2
    while len(L) < k:  # tant qu'on n'a pas atteint le bon nombre de contre-exemples on continue
        if TestFermat2(n) == (False,True): # si n n'est pas premier mais Fermat-premier on l'ajoute
            L = L+[n]
        n = n+1
    return L

In [194]:
contreExemples2(5)

[561, 1105, 1729, 2465, 2821]

In [247]:
# on tire un nombre a au hasard et on teste la condition (1) du TP pour ce nombre
def TestFermatP(n):
    a = randint(1,n-1) # entier aléatoire entre 1 et n-1
    if math.gcd(a,n) !=1 or ExpRapide(a,n-1,n) != 1:
        return False
    return True

In [248]:
TestFermatP(6)

False

In [197]:
n = 10**2022

# on mesure le temps de calcul pour l'algo TestFermat
start=time.time()

TestFermat(n)

end=time.time()
duree=end-start
print(duree)

# on mesure maintenant le temps de calcul pour TestFermatP
start=time.time()

TestFermatP(n)

end=time.time()
duree=end-start
print(duree)

1.5014634132385254
1.3357200622558594


In [249]:
# algo intermédiaire utilisé dans TestMillerRabin
#  Entrée : entier n impair.
# On renvoie h et N tels que n = 1 + 2^h*m avec m impair
def decompoMiller(n):
    h = 0
    m = n-1
    while m%2 == 0:
        h = h+1
        m = m//2
    return (h,m)

In [250]:
# algo intermédiaire utilisé dans TestMillerRabin
# On construit la liste des a^{2^k*m} mod n avec k entre 0 et h (où m et h sont donnés par l'algo précédent)

def CreationListe(n,a):
    (h,m) = decompoMiller(n)  # rappel : n = 1+2^h*m
    L = [ExpRapide(a,m,n)]    # on initialise en calculant a^m mod n
    for i in range(h):        # le terme L[i+1] est simplement L[i]^2
        L = L+[(L[i]**2)%n]
    return L

In [251]:
# renvoie True si la liste ne contient que des 1, False sinon
def testListe1(L):
     return L.count(1) == len(L)

In [257]:
# algo récursif pour tester si la liste est de la forme [*,...,*,n-1,1,...,1]
def testListe2(L,n):
    # si on a la bonne forme, L termine au minimum par n-1,1, donc sa longueur est >= 2
    if len(L) < 2:     
        return False
    # Si L commence par n-1 et ensuite ne contient que des 1, c'est bon
    if L[0] == n-1 and L.count(1) == len(L) - 1:
        return True
    # Sinon, on supprime le premier terme et on applique l'algo à la liste tronquée
    G = L[1:]  # subtilité ici : on fait une copie de L pour éviter que notre algo ne modifie L!
    return testListe2(G, n)

In [258]:
# Remarquons que si a^{2^k*m} = n-1 mod n, alors toutes les valeurs suivantes valent 1
# Donc pour tester si la liste CreationListe(n,a) a la forme 2, il suffit simplement
# de vérifier que n-1 appartient à la liste ! Cela donne le programme simplifié suivant :

# algo récursif pour tester si la liste est de la forme [*,...,*,n-1,1,...,1]
def testListe2bis(L,n):
    G = L[:-1]  # On fait une copie de L en supprimant le dernier élément pour éviter que notre algo ne modifie L
    return n-1 in G

In [261]:
# prend en entrée n. Renvoie True si n vérifie la condition (2) du TP, False sinon

def TestMillerRabin(n):
    if n%2 == 0 and n > 2: # Si n est pair > 2, on renvoie directement False
        return False
    a = randint(1,n-1)
    L = CreationListe(n,a)
    if math.gcd(a,n) != 1:
        return False
    return (math.gcd(a,n) == 1) and (testListe1(L) or testListe2(L,n))
        
    # si pgcd(a,n) != 1, renvoie False.
    # Si pgcd(a,n) = 1, renvoie True dès que L est du type 1 ou du type 1, renvoie False sinon

In [262]:
print(TestMillerRabin(11))  # TestMillerRabin(n) est toujours vrai pour n premier
print(TestMillerRabin(4))

True
False


In [263]:
testListe2([4,1,1,5,4,1,1,1],5)

True

In [264]:
n = 100129*200257

N = 10000 # nombre de répétitions
nbFalse = 0 # on compte les fois où on obtient False

for k in range(N):
    if not TestMillerRabin(n):
        nbFalse = nbFalse + 1

print(nbFalse/N)  # On fait la moyenne. On constate que cette moyenne est >= 0.75

0.8279


In [265]:
# renvoie True si n passe le test de Miller-Rabin pour k répétitions indépendantes
# on se sert de cet algo dans CribleMR
def TestMillerRabinR(n,k):
    j = 0
    while TestMillerRabin(n) and j < k:
        j = j+1
    return j == k # on renvoie True si on a passé les k tests
        

In [266]:
# renvoie la liste des entiers <= N qui ont passé k fois le test de Miller-Rabin avec succès
def CribleMR(N,k):
    L = []
    for n in range(2,N+1):
        if TestMillerRabinR(n,k):
            L = L+[n]
    return L

In [267]:
# CribleMR(N,k) contient la liste Crible(N) des premiers <= N
# Pour comparer ces listes, il suffit donc de comparer leur nombre d'éléments

print("Comparaison entre crible(1000) et CribleMR(1000,k)")
print("On affiche k et la différence des longueurs")

N = 1000
nbPrime = len(crible(N))

for k in range(1,11):
    print(k, len(CribleMR(N,k)) - nbPrime)

Comparaison entre crible(1000) et CribleMR(1000,k)
On affiche k et la différence des longueurs
1 9
2 1
3 0
4 0
5 0
6 0
7 0
8 0
9 0
10 0


In [268]:
# renvoie le plus petit p >= m passant avec succès 10 fois le test de Miller-Rabin
def PremierSuivant(m):
    p = m
    while not TestMillerRabinR(p,10):
        p = p+1
    return p

In [269]:
PremierSuivant(1000)

1009

In [270]:
# on suppose ici n impair
# on renvoie la (r,L), où L est la liste des a ne vérifiant pas la condition (2) du TP
# et r = longueur de L (donc = nombre de témoins)

def TemoinsMR(n):
    G = []   # liste des a ne vérifiant pas (2)
    for a in range(1,n):
        L = CreationListe(n,a)
        if not (testListe1(L) or testListe2bis(L,n)):
            G = G+[a]
    return len(G),G

In [271]:
# on suppose ici n impair
# on renvoie la (r,L), où L est la liste des a ne vérifiant pas la condition (2) du TP
# et r = longueur de L (donc = nombre de témoins)
# c'est le même algo que précédemment mais un peu plus optimisé sans faire appel aux sous-algo

def TemoinsMR2(n):
    (h,m) = decompoMiller(n)
    L = []   # liste des a ne vérifiant pas (2)
    for a in range(1,n):
        M = ExpRapide(a,m,n)
        if M != 1:  # on teste si la première condition de (2) est fausse
            k = 0
            while M != n-1 and k < h:  # on teste si la 2ème condition de (2) est fausse
                M = M**2%n
                k = k+1
            if k == h:    # si k = h c'est que (2) est fausse pour tout k < h
                L = L+[a]
    return len(L),L
                
       

In [272]:
n = 15
print(TemoinsMR(n))
print(TemoinsMR2(n))

(12, [2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13])
(12, [2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13])


In [276]:
n = 25
print("Liste des témoins pour n=25")
print(TemoinsMR(n))

print(" ")
print("Les non-témoins sont 7, 18 et 24")

print(" ")
print("On affiche à la main la liste des a^{2^km} mod n")
for a in range(1,n):
    print(a,CreationListe(n,a))

Liste des témoins pour n=25
(20, [2, 3, 4, 5, 6, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 19, 20, 21, 22, 23])
 
Les non-témoins sont 7, 18 et 24
 
On affiche à la main la liste des a^{2^km} mod n
1 [1, 1, 1, 1]
2 [8, 14, 21, 16]
3 [2, 4, 16, 6]
4 [14, 21, 16, 6]
5 [0, 0, 0, 0]
6 [16, 6, 11, 21]
7 [18, 24, 1, 1]
8 [12, 19, 11, 21]
9 [4, 16, 6, 11]
10 [0, 0, 0, 0]
11 [6, 11, 21, 16]
12 [3, 9, 6, 11]
13 [22, 9, 6, 11]
14 [19, 11, 21, 16]
15 [0, 0, 0, 0]
16 [21, 16, 6, 11]
17 [13, 19, 11, 21]
18 [7, 24, 1, 1]
19 [9, 6, 11, 21]
20 [0, 0, 0, 0]
21 [11, 21, 16, 6]
22 [23, 4, 16, 6]
23 [17, 14, 21, 16]
24 [24, 1, 1, 1]
